In [6]:
import pandas as pd
import numpy as np
import sys
sys.path.insert(0,'..')
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [14]:
from generate_segment_trajectories import GenerateSegmentTrajectories, get_agent_ids,get_max_frame_value, get_basic_dataframe, get_dtw_maps

In [15]:
normal = get_dtw_maps(rounds=["round_0"],agent_map_folder="../agent_maps", max_dtw_maps=150)

0 frame id
0 frame id
0 frame id
0 frame id
0 frame id
0 frame id
0 frame id
0 frame id
0 frame id
0 frame id
0 frame id
0 frame id


In [23]:
anomalous = get_dtw_maps(rounds=["debris_round2"],agent_map_folder="../agent_maps", max_dtw_maps=10000)

In [18]:
print(len(anomalous))
anomalous[0].shape
#unsqueeze an concat dim0

151


(10, 25, 25)

In [21]:
len(normal)

151

In [24]:
len(anomalous)

426

In [28]:
anomalous

frame_id       round_id  ego_agent_id  num_vehicles  max_velocity_x  \
0          0  debris_round2             4           305             0.0   
1          1  debris_round2             2           305             0.0   
2          2  debris_round2             2           305             0.0   
3          3  debris_round2             2           305             0.0   
4          4  debris_round2             2           305             0.0   
..       ...            ...           ...           ...             ...   
21       295  debris_round2             2           323             0.0   
22       296  debris_round2             2           323             0.0   
23       297  debris_round2             2           323             0.0   
24       298  debris_round2             2           323             0.0   
25       299  debris_round2             2           323             0.0   

    max_velocity_y  max_velocity_z  max_ang_velocity_x  max_ang_velocity_y  \
0     0.000000e+00             0.0                 0.0                 0.0   
1     0.000000e+00             0.0                 0.0                 0.0   
2     0.000000e+00             0.0                 0.0                 0.0   
3     0.000000e+00             0.0                 0.0                 0.0   
4     5.599654e-08             0.0                 0.0                 0.0   
..             ...             ...                 ...                 ...   
21    0.000000e+00             0.0                 0.0                 0.0   
22    0.000000e+00             0.0                 0.0                 0.0   
23    0.000000e+00             0.0                 0.0                 0.0   
24    0.000000e+00             0.0                 0.0                 0.0   
25    0.000000e+00             0.0                 0.0                 0.0   

    max_ang_velocity_z  ...  min_velocity_z  min_ang_velocity_x  \
0                  0.0  ...       -0.489837            0.000000   
1                  0.0  ...       -0.979429            0.000000   
2                  0.0  ...       -1.468776            0.000000   
3                  0.0  ...       -1.957878            0.000000   
4                  0.0  ...       -1.283988           -0.000006   
..                 ...  ...             ...                 ...   
21                 0.0  ...        0.000000            0.000000   
22                 0.0  ...        0.000000            0.000000   
23                 0.0  ...        0.000000            0.000000   
24                 0.0  ...        0.000000            0.000000   
25                 0.0  ...        0.000000            0.000000   

    min_ang_velocity_y  min_ang_velocity_z  max_acc_x  max_acc_y  max_acc_z  \
0         0.000000e+00        0.000000e+00        0.0   0.000000   0.000000   
1         0.000000e+00        0.000000e+00        0.0   0.000000   0.000000   
2         0.000000e+00        0.000000e+00        0.0   0.000000   0.000000   
3         0.000000e+00        0.000000e+00        0.0   0.000000   0.000000   
4        -9.210367e-07       -1.076592e-09        0.0   0.000001  13.477802   
..                 ...                 ...        ...        ...        ...   
21        0.000000e+00        0.000000e+00        0.0   0.000000   0.000000   
22        0.000000e+00        0.000000e+00        0.0   0.000000   0.000000   
23        0.000000e+00        0.000000e+00        0.0   0.000000   0.000000   
24        0.000000e+00        0.000000e+00        0.0   0.000000   0.000000   
25        0.000000e+00        0.000000e+00        0.0   0.000000   0.000000   

       min_acc_x  min_acc_y  min_acc_z  
0   0.000000e+00        0.0  -9.796735  
1   0.000000e+00        0.0  -9.791836  
2   0.000000e+00        0.0  -9.786944  
3   0.000000e+00        0.0  -9.782043  
4  -9.287096e-08        0.0   0.000000  
..           ...        ...        ...  
21  0.000000e+00        0.0   0.000000  
22  0.000000e+00        0.0   0.000000  
23  0.000000e+00        0.0   0.000000  
24

# Train and test the Random forest model

In [42]:
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split

In [50]:
# useful_cols = ["num_vehicles", "max_velocity_x", "max_velocity_y", 
#         "max_velocity_z", "max_ang_velocity_x", "max_ang_velocity_y", "max_ang_velocity_z", "min_velocity_x", 
#         "min_velocity_y", "min_velocity_z", "min_ang_velocity_x", "min_ang_velocity_y", "min_ang_velocity_z", 
#         "max_acc_x", "max_acc_y", "max_acc_z", "min_acc_x","min_acc_y","min_acc_z"]
useful_cols = ["max_velocity_x", "max_velocity_y", 
        "max_velocity_z", "max_ang_velocity_x", "max_ang_velocity_y", "max_ang_velocity_z", "min_velocity_x", 
        "min_velocity_y", "min_velocity_z", "min_ang_velocity_x", "min_ang_velocity_y", "min_ang_velocity_z", 
        "max_acc_x", "max_acc_y", "max_acc_z", "min_acc_x","min_acc_y","min_acc_z"]

X = pd.concat([normal[useful_cols],anomalous[useful_cols]])
y = np.hstack([np.zeros(normal.shape[0]),np.ones(anomalous.shape[0])])

In [51]:
X.shape, y.shape

((7605, 18), (7605,))

In [52]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=42)
X_train.shape, X_test.shape, y_train.shape, y_test.shape 

((5323, 18), (2282, 18), (5323,), (2282,))

In [53]:
RF = RandomForestClassifier(n_estimators=1000, max_depth=10, random_state=0)

In [54]:
RF_res = RF.fit(X_train, y_train)
RF_res.predict(X_test)
round(RF_res.score(X_test, y_test), 4)

0.9899

In [57]:
RF_res.score(X_test, y_test)

0.9899211218229623

In [41]:
X_test

num_vehicles  max_velocity_x  max_velocity_y  max_velocity_z  \
19           257        0.000024       -0.000003        0.000002   
2            257        2.497234       -4.201942        0.051143   
1            317       -0.238521        6.747624       -1.130662   
7            256       -4.881981       -0.218979       -0.000003   
22           258        0.064626       -4.188365        0.813381   
..           ...             ...             ...             ...   
14           305        2.380898        0.000000        0.000000   
8            320       -0.052494       -6.797880       -0.099608   
2            258        0.149118       -0.090043        0.051011   
3            320       -0.024026       -6.753898        0.013471   
10           257        0.000000        0.000000        0.000000   

    max_ang_velocity_x  max_ang_velocity_y  max_ang_velocity_z  \
19            0.000126            0.000031           -0.000094   
2             0.328501            0.193119            6.314550   
1            -0.047881           -0.001434            0.000575   
7            -0.177714           -0.007944            2.175142   
22           -0.000715           -0.059009           -0.268477   
..                 ...                 ...                 ...   
14            3.499997            3.249607            0.000000   
8             0.022837            0.097039            6.129976   
2             0.934421            2.645389            0.352769   
3            -0.032046           -0.001135            0.074287   
10            0.627568            0.156069            0.010069   

    min_velocity_x  min_velocity_y  min_velocity_z  min_ang_velocity_x  \
19        0.000010       -0.000012       -0.000005           -0.000015   
2         2.497234       -4.201942        0.051143            0.328501   
1        -0.238521        6.747624       -1.130662           -0.047881   
7        -4.881981       -0.218979       -0.000003           -0.177714   
22        0.064626       -4.188365        0.813381           -0.000715   
..             ...             ...             ...                 ...   
14        0.000000       -1.618212       -0.002874            0.000000   
8        -0.052494       -6.797880       -0.099608            0.022837   
2        -2.553805       -3.966323       -0.016439           -0.291650   
3        -0.024026       -6.753898        0.013471           -0.032046   
10       -0.039139       -4.855679       -0.038202           -0.525050   

    min_ang_velocity_y  min_ang_velocity_z  max_acc_x     max_acc_y  \
19           -0.000088           -0.000297   0.000001  7.413337e-07   
2             0.193119            6.314550   0.217565  1.215720e-01   
1            -0.001434            0.000575   0.005651 -1.624012e-01   
7            -0.007944            2.175142   0.008557 -1.981984e-01   
22           -0.059009           -0.268477  -0.009542 -1.006126e-03   
..                 ...                 ...        ...           ...   
14            0.000000           -0.041124   0.000000  8.972044e+00   
8             0.097039            6.129976   0.634591  7.156372e-02   
2             0.040448            0.029288  -0.056903  1.538785e+00   
3            -0.001135            0.074287   0.008965  1.020527e-01   
10           -1.026942           -0.065212   0.000000  2.322197e-03   

    max_acc_z  min_acc_x  min_acc_y  min_acc_z  
19   0.000025  -0.000001  -0.000004  -0.000029  
2    0.030215   0.217565   0.121572   0.030215  
1    0.027308   0.005651  -0.162401   0.027308  
7   -0.000001   0.008557  -0.198198  -0.000001  
22   0.000343  -0.009542  -0.001006   0.000343  
..        ...        ...        ...        ...  
14   0.054130 -13.129854   0.000000   0.000000  
8    0.001092   0.634591   0.071564   0.001092  
2   -0.019894  -1.623156  -0.049769  -0.041082  
3    0.070742   0.008965   0.102053   0.070742  
10   0.021071  -0.015998  -0.281520  -0.013809  

[2282 rows x 19 columns]

# Visualize one of the Random forest Trees

In [56]:
# Extract single tree
estimator = RF_res.estimators_[5]

from sklearn.tree import export_graphviz
# Export as dot file
export_graphviz(estimator, out_file='tree.dot', 
                feature_names = X_train.columns,
                class_names = ["Normal","Anomalous"],
                rounded = True, proportion = False, 
                precision = 2, filled = True)

# Convert to png using system command (requires Graphviz)
from subprocess import call
call(['dot', '-Tpng', 'tree.dot', '-o', 'tree.png', '-Gdpi=600'])

# Display in jupyter notebook
from IPython.display import Image
Image(filename = 'tree.png')